<a href="https://colab.research.google.com/github/iaakopyan/SPPR/blob/master/lab2.1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import numpy as np
import pandas as pd

In [ ]:
!pip install surprise

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 771 kB 4.9 MB/s 
  Created wheel for scikit-surprise: filename=scikit_surprise-1.1.3-cp38-cp38-linux_x86_64.whl size=2626454 sha256=3449afa68ea4e38a65403d468f3e82261f94ed9b009847c8debe215a68b8d72c
  Stored in directory: /root/.cache/pip/wheels/af/db/86/2c18183a80ba05da35bf0fb7417aac5cddbd93bcb1b92fd3ea
Successfully built scikit-surprise


In [ ]:
import os
import pandas as pd
import numpy as np
from surprise import *
from surprise.model_selection import KFold
from surprise.model_selection import cross_validate
from surprise.accuracy import rmse
from surprise.model_selection import train_test_split
from surprise.model_selection import GridSearchCV
from collections import defaultdict
from surprise import accuracy

In [ ]:
books_ratings = pd.read_csv('BX-Book-Ratings.csv', sep=',', encoding='latin-1', error_bad_lines=False)

/usr/local/lib/python3.8/dist-packages/IPython/core/interactiveshell.py:3326: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version.


  exec(code_obj, self.user_global_ns, self.user_ns)


In [ ]:
books = pd.read_csv('BX_Books.csv', sep=',', encoding='latin-1', error_bad_lines=False)

/usr/local/lib/python3.8/dist-packages/IPython/core/interactiveshell.py:3326: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version.


  exec(code_obj, self.user_global_ns, self.user_ns)
b'Skipping line 10824: expected 8 fields, saw 9\nSkipping line 14769: expected 8 fields, saw 9\nSkipping line 14936: expected 8 fields, saw 9\nSkipping line 15690: expected 8 fields, saw 10\nSkipping line 17320: expected 8 fields, saw 9\nSkipping line 18095: expected 8 fields, saw 9\nSkipping line 28443: expected 8 fields, saw 9\nSkipping line 33098: expected 8 fields, saw 9\nSkipping line 36394: expected 8 fields, saw 12\nSkipping line 42628: expected 8 fields, saw 9\nSkipping line 43667: expected 8 fields, saw 10\nSkipping line 52174: expected 8 fields, saw 9\nSkipping line 56901: expected 8 fields, saw 10\nSkipping line 58600: expected 8 fields, saw 10\nSkipping line 60739: expected 8 fields, saw 10\n'
b'Skipping line 65756: expected 8 fields, saw 9\

In [ ]:
books.head()

ISBN                                         Book-Title  \
0  0195153448                                Classical Mythology   
1  0002005018                                       Clara Callan   
2  0060973129                               Decision in Normandy   
3  0374157065  Flu: The Story of the Great Influenza Pandemic...   
4  0393045218                             The Mummies of Urumchi   

            Book-Author  Year-Of-Publication                Publisher  \
0    Mark P. O. Morford                 2002  Oxford University Press   
1  Richard Bruce Wright                 2001    HarperFlamingo Canada   
2          Carlo D'Este                 1991          HarperPerennial   
3      Gina Bari Kolata                 1999     Farrar Straus Giroux   
4       E. J. W. Barber                 1999   W. W. Norton & Company   

                                         Image-URL-S  \
0  http://images.amazon.com/images/P/0195153448.0...   
1  http://images.amazon.com/images/P/0002005018.0...   
2  http://images.amazon.com/images/P/0060973129.0...   
3  http://images.amazon.com/images/P/0374157065.0...   
4  http://images.amazon.com/images/P/0393045218.0...   

                                         Image-URL-M  \
0  http://images.amazon.com/images/P/0195153448.0...   
1  http://images.amazon.com/images/P/0002005018.0...   
2  http://images.amazon.com/images/P/0060973129.0...   
3  http://images.amazon.com/images/P/0374157065.0...   
4  http://images.amazon.com/images/P/0393045218.0...   

                                         Image-URL-L  
0  http://images.amazon.com/images/P/0195153448.0...  
1  http://images.amazon.com/images/P/0002005018.0...  
2  http://images.amazon.com/images/P/0060973129.0...  
3  http://images.amazon.com/images/P/0374157065.0...  
4  http://images.amazon.com/images/P/0393045218.0...

In [ ]:
books_ratings.head()

UserID        ISBN  BookRating
0  276725  034545104X           0
1  276726  0155061224           5
2  276727  0446520802           0
3  276729  052165615X           3
4  276729  0521795028           6

In [ ]:
books_books = pd.read_csv('BX_Books.csv')

UnicodeDecodeError: ignored

In [ ]:
f = open('BX_Books.csv')
for i in f:
    print(i)

"ISBN","Book-Title","Book-Author","Year-Of-Publication","Publisher","Image-URL-S","Image-URL-M","Image-URL-L"

"0195153448","Classical Mythology","Mark P. O. Morford","2002","Oxford University Press","http://images.amazon.com/images/P/0195153448.01.THUMBZZZ.jpg","http://images.amazon.com/images/P/0195153448.01.MZZZZZZZ.jpg","http://images.amazon.com/images/P/0195153448.01.LZZZZZZZ.jpg"

"0002005018","Clara Callan","Richard Bruce Wright","2001","HarperFlamingo Canada","http://images.amazon.com/images/P/0002005018.01.THUMBZZZ.jpg","http://images.amazon.com/images/P/0002005018.01.MZZZZZZZ.jpg","http://images.amazon.com/images/P/0002005018.01.LZZZZZZZ.jpg"

"0060973129","Decision in Normandy","Carlo D'Este","1991","HarperPerennial","http://images.amazon.com/images/P/0060973129.01.THUMBZZZ.jpg","http://images.amazon.com/images/P/0060973129.01.MZZZZZZZ.jpg","http://images.amazon.com/images/P/0060973129.01.LZZZZZZZ.jpg"

"0374157065","Flu: The Story of the Great Influenza Pandemic of 1918 and

UnicodeDecodeError: 'utf-8' codec can't decode byte 0xc3 in position 1190: invalid continuation byte

In [ ]:

reader = Reader(line_format='user item rating', sep="\t")
reader = Reader(rating_scale=(0.5, 10.0))
df = Dataset.load_from_df(books_ratings, reader)

In [ ]:
def configure_plotly_browser_state():
  import IPython
  display(IPython.core.display.HTML('''
        
        
        '''))


In [ ]:
configure_plotly_browser_state()
from plotly.offline import init_notebook_mode, plot, iplot
import plotly.graph_objs as go

init_notebook_mode(connected = True)

data = books_ratings["BookRating"].value_counts().sort_index(ascending=False)
trace = go.Bar(x = data.index,
               text = ['{:.1f} %'.format(val) for val in (data.values / books_ratings.shape[0] * 100)],
               textposition = 'auto',
               textfont = dict(color = '#000000'),
               y = data.values,
               )
# Create layout
layout = dict(title = 'Distribution Of {} ratings'.format(books_ratings.shape[0]),
              xaxis = dict(title = 'Rating'),
              yaxis = dict(title = 'Count'))
# Create plot
fig = go.Figure(data=[trace], layout=layout)
iplot(fig)
     

In [ ]:
configure_plotly_browser_state()


data = books_ratings.groupby('ISBN')['BookRating'].count().clip(upper=50)
# Create trace
trace = go.Histogram(x = data.values,
                     name = 'Ratings',
                     xbins = dict(start = 0,
                                  end = 50,
                                  size = 2))
# Create layout
layout = go.Layout(title = 'Distribution Of Number of Ratings Per Item (Clipped at 50)',
                   xaxis = dict(title = 'Number of Ratings Per Item'),
                   yaxis = dict(title = 'Count'),
                   bargap = 0.2)

# Create plot
fig = go.Figure(data=[trace], layout=layout)
iplot(fig)


In [ ]:
data.head()

ISBN
 0330299891    2
 0375404120    2
 0586045007    1
 9022906116    2
 9032803328    1
Name: BookRating, dtype: int64

In [ ]:

!pip install plotly
     

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:

configure_plotly_browser_state()
from plotly.offline import init_notebook_mode, plot, iplot
import plotly.graph_objs as go

init_notebook_mode(connected = True)

## **Вот эта часть кода снизу, которая меня бесит**

In [ ]:

param_grid = {'n_factors': [25, 30, 35, 40], 'n_epochs': [15, 20, 25], 'lr_all': [0.001, 0.003, 0.005, 0.008],
              'reg_all': [0.08, 0.1, 0.15]}
gs = GridSearchCV(SVD, param_grid, measures=['rmse', 'mae'], cv=3)

gs.fit(df)

algo = gs.best_estimator['rmse']
print(gs.best_score['rmse'])
print(gs.best_params['rmse'])

#Assigning values
t = gs.best_params
factors = t['rmse']['n_factors']
epochs = t['rmse']['n_epochs']
lr_value = t['rmse']['lr_all']
reg_value = t['rmse']['reg_all']

In [ ]:

trainset, testset = train_test_split(data, test_size=0.25)
algo = SVD(n_factors=40, n_epochs=25, lr_all=0.008, reg_all=0.08)
predictions = algo.fit(trainset).test(testset)
accuracy.rmse(predictions)

In [ ]:
def get_Iu(uid):
    """ 
    args: 
      uid: the id of the user
    returns: 
      the number of items rated by the user
    """
    try:
        return len(trainset.ur[trainset.to_inner_uid(uid)])
    except ValueError: # user was not part of the trainset
        return 0
    
def get_Ui(iid):
    """ 
    args:
      iid: the raw id of the item
    returns:
      the number of users that have rated the item.
    """
    try: 
        return len(trainset.ir[trainset.to_inner_iid(iid)])
    except ValueError:
        return 0

    
df_predictions = pd.DataFrame(predictions, columns=['uid', 'iid', 'rui', 'est', 'details'])
df_predictions['Iu'] = df_predictions.uid.apply(get_Iu)
df_predictions['Ui'] = df_predictions.iid.apply(get_Ui)
df_predictions['err'] = abs(df_predictions.est - df_predictions.rui)


In [ ]:
df_predictions.head()

In [ ]:
best_predictions = df_predictions.sort_values(by='err')[:10]
worst_predictions = df_predictions.sort_values(by='err')[-10:]


In [ ]:
temp = books_ratings.loc[books_ratings['ISBN'] == 3996]['rating']
configure_plotly_browser_state()

# Create trace
trace = go.Histogram(x = temp.values,
                     name = 'Ratings',
                     xbins = dict(start = 0,
                                  end = 5, size=.3))
 # Create layout
layout = go.Layout(title = 'Number of ratings item 3996 has received',
                   xaxis = dict(title = 'Number of Ratings Per Item'),
                   yaxis = dict(title = 'Count'),
                   bargap = 0.2)
# Create plot
fig = go.Figure(data=[trace], layout=layout)
iplot(fig)